In [42]:
import json
import pandas as pd
from collections import Counter
import ast
import numpy as np
import matplotlib.pyplot as plt
import pickle
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction import text
from scipy.sparse.linalg import svds
from sklearn.preprocessing import normalize

In [2]:
f = open('backend/dataset/wiki_scraping/wiki_texts.json')
wiki_texts = json.load(f)

In [3]:
big_df = pd.read_csv('backend/dataset/big_df_edited.csv')

In [4]:
big_df.drop(columns=['Unnamed: 0'], inplace=True)

In [5]:
big_df['tknzd_lyrics'] = big_df['tknzd_lyrics'].apply(ast.literal_eval)
big_df['emotions'] = big_df['emotions'].apply(ast.literal_eval)
big_df['social_tags'] = big_df['social_tags'].apply(ast.literal_eval)

In [6]:
big_df.shape

(34462, 14)

In [27]:
for i in big_df['social_tags']:
    print([x[0] for x in i])

['hip-hop', 'rap', 'lil wayne', 'a milli a milli a milli a milli a milli a milli a milli a milli a milli a milli a milli', 'hip hop', 'tougher than nigerian hair', 'lolli pop', 'new orleans', 'best rapper alive', 'fav', 'milli', 'what the fuck is going on here', '2008', 'favorites', 'dirty south', 'southern rap', 'gangsta rap', 'sonic rock', 'freestyle', 'aitch', 'aitchrap', 'aitchsonic', 'usa hot rnb hip hop songs number one hit', 'hell yeah', 'best of 2008', 'moonh8sun', 'tha carter iii', 'party music', 'gangsta cruisen', 'lil wayne - a milli', 'great', 'southern', 'aitchchill', 'fuck', 'hiphop', 'lyricist', 'omg my head just exploded', 'pitchfork top 100 tracks of 2008', 'blaze to this one', 'at least its not miracles', 'songs i should hate but secretly like', 'miniature weezy', 'straightbootylicious', 'cash money records', 'epic', 'amillie', 'rap and hip-hop', 'boy diz son gis hard i neva get tried of it', 'dirty filthy yeah', 'phat', 'gangsta and hardcore', 'american', 'louisiana'

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['singer-songwriter', 'rock', 'great melodies', 'beautiful', 'favorites', 'blue songs', 'ryan adams', 'loveishellish', 'alt country', 'spring 2006', 'beautiful sad', 'melancholic', 'american', 'heartbreakingly beautiful', 'sad', 'alternative', 'sundaymusic', 'songs i love to sing', 'alt singer songwriter', 'words fail to describe', 'so beautiful it hurts', 'fill in the blank blues', 'absolute killer', 'so so sad', 'nostalgico', 'at ease', 'grey room', 'mbo-song', 'sternmusik', 'i am so fucking sad', 'ligue pro meu terapeuta se eu estiver ouvindo no repeat', 'ladenmusik', 'alt-country', 'folk', 'indie', 'awesome', 'favorite songs', 'british', 'air', 'fav', 'other', 'repeat', '00s', 'male vocalists', 'quiet storm', 'heartwrenching', 'songs i love', 'colors', 'muso', 'fucking brilliant', 'heart wrenching', 'ryan loves', 'colour', 'tantotempotaste']
['angela bofill', 'soul', 'slow jams', 'old school slow jams', 'rnb', 'love songs', '80s soul', 'quiet storm classics', 'romantic ballad', 'ro

['garage rock', 'garage', 'melancholy', 'best song ever', 'i feel good', 'de avonden', 'brown music']
['christmas', 'instrumental', 'oldies', 'easy listening', 'xmas', 'scottish melodies', 'hogmany', 'easy listening orchestra', 'orchestra - strings', 'orchestra - 7', 'schoene schlager', 'musica instrumental', 'relaxing piano', 'oldis', 'music for me', 'big bands', 'tobuy', 'relaxing instrumental', 'mooi', 'memories', 'easy', 'feelings', 'smooth', 'favourite', 'jazz', 'soft rock', 'pasko', 'x-mas', 'amerika', '60s']
['80s', 'metal', 'usa', 'energetic']
['jazz', 'fusion', 'magna carta records', 'covers', 'good drums', 'jazzy covers', 'jazz guitar', 'chill', 'cover', 'jazz metal', 'jazz fusion', 'rush', 'interesting', 'fury', 'rush cover', 'unstopable', 'euro jazz', 'progressive', 'funky', 'jazzy kewl']
['samba', 'female vocalists', 'bossa nova', 'jazz', 'cafe at place vendome', 'smooth', 'cocktails at sunset', 'british', 'jazz vocal', 'chill', 'brasil', 'female jazz vocalist', 'chillboss

In [30]:
big_df['combo_tags'] = big_df['emotions'] + big_df['social_tags'].apply(lambda l: [x[0] for x in l])

In [31]:
big_df

title  tag           artist  year    views features  \
0                A Milli  rap        Lil Wayne  2008  1237174       {}   
1        The Documentary  rap         The Game  2005   236542       {}   
2             My Name Is  rap           Eminem  1999  1464039       {}   
3            We Fly High  rap        Jim Jones  2006    63337       {}   
4        Keys Open Doors  rap           Clipse  2006    61909       {}   
...                  ...  ...              ...   ...      ...      ...   
34457  Taste For Harmony  pop  Union Of Knives  2006        5       {}   
34458            Gravity  pop   Brenda Russell  1988        2       {}   
34459      Floating Free  pop      Vibrasphere  2010        1       {}   
34460        Grey Matter  pop            Jewel  2001        8       {}   
34461           Spitfire  pop  Bertine Zetlitz  2001        1       {}   

                                                  lyrics       id  \
0      [Intro]\nBangladesh\nYoung Money!\nYou dig?\nM...       59   
1      [Intro: Livin' tha Life (2003)]\nBitch, I want...       63   
2      [Produced by Dr. Dre]\n\n[Chorus: Eminem]\nHi,...       68   
3      [Intro: Sample & Jim Jones]\nI wear a mean dar...       80   
4      [Chorus: Pusha T]\nKeys open doors, keys open ...      116   
...                                                  ...      ...   
34457  Trust me\nI know where I'm going\nIt won't be\...  7817131   
34458  [Verse 1: Brenda]\nIf it's love that brought u...  7840324   
34459  I wanna do it\nI'm gonna do it\nI wanna do it\...  7852356   
34460  [Intro]\nI hate you, I love you\nLeave, don't ...  7870813   
34461  Be careful little girl\nBefore you rock his wo...  7874259   

                  song_id               emotions  \
0      TRFASZI128F93229B7                [party]   
1      TRECLHK128E0784A19               [tragic]   
2      TROVBAL12903CC4F1B    [funny, fun, party]   
3      TRTJQTZ128F92F4A64         [party, happy]   
4      TRBSYSE128F42BBDCF  [dark, smooth, tense]   
...                   ...                    ...   
34457  TRCAWPX128F1479233          [melancholic]   
34458  TRXCBHR128F42B226B                  [fun]   
34459  TRDERZZ128F93350F5          [sexy, relax]   
34460  TRLMRUW128F9330A10                 [calm]   
34461  TRJZTLD128F4272833                 [dark]   

                                             social_tags  \
0      [(hip-hop, 100), (rap, 87), (lil wayne, 78), (...   
1      [(rap, 100), (hip-hop, 71), (the game, 71), (t...   
2      [(rap, 100), (hip-hop, 73), (eminem, 65), (hip...   
3      [(hip-hop, 100), (rap, 93), (hip hop, 50), (ba...   
4      [(hip-hop, 100), (the neptunes, 58), (neptunes...   
...                                                  ...   
34457  [(trylove, 100), (love, 100), (indie, 100), (t...   
34458  [(soul, 100), (groovy, 33), (fun, 33), (love s...   
34459  [(progressive trance, 100), (psytrance, 83), (...   
34460  [(alternative, 100), (pop, 50), (love, 25), (f...   
34461  [(weird, 100), (ladies, 100), (pop, 50), (fema...   

                                            tknzd_lyrics  log_views  \
0      [bangladesh, young, money, you, dig, mack, im,...  14.028341   
1      [bitch, i, want, my, mother, fuckin, money, ba...  12.373885   
2      [hi, my, name, is, what, my, name, is, who, my...  14.196710   
3      [i, wear, a, mean, dark, pair, of, shades, and...  11.056241   
4      [keys, open, doors, keys, open, doors, keys, o...  11.033437   
...                                                  ...        ...   
34457  [trust, me, i, know, where, im, going, it, won...   1.791759   
34458  [if, its, love, that, brought, us, together, w...   1.098612   
34459  [i, wanna, do, it, im, gonna, do, it, i, wanna...   0.693147   
34460  [i, hate, you, i, love, you, leave, dont, go, ...   2.197225   
34461  [be, careful, little, girl, before, you, rock,...   0.693147   

       norm_views                                         combo_tags  
0        0.874590  [party, hip-

In [43]:
unique_tags = set([j for sub in big_df['combo_tags'].values for j in sub])

In [45]:
tag_to_index = {t: i for i, t in enumerate(unique_tags)}
index_to_tag = {i: t for i, t in enumerate(unique_tags)}

In [46]:
song_tag_mat = np.zeros((big_df.shape[0], len(unique_tags)))
for i in range(big_df.shape[0]):
    tags = big_df['combo_tags'].iloc[i]
    for t in tags:
        j = tag_to_index[t]
        song_tag_mat[i, j] = 1

In [ ]:
N_FEATS = 40
docs_compressed, s, words_compressed = svds(song_tag_mat, k=N_FEATS)
words_compressed = words_compressed.transpose()
words_compressed_normed = normœalize(words_compressed, axis=1)
docs_compressed_normed = normalize(docs_compressed, axis=1)